In [1]:
import pandas as pd
import numpy as np
import datetime
import time
import joblib
import os
from datetime import date
#資料庫
from influxdb import InfluxDBClient
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler
from sklearn.linear_model import LinearRegression
from sklearn.svm import SVC, SVR
from sklearn_rvm import EMRVC
from sklearn_rvm import EMRVR
import xgboost as xgb
import lightgbm as lgb
#載入模型
import joblib
#繪圖工具
import plotly.graph_objects as go
import matplotlib.dates as md
from tqdm import tqdm

In [2]:
# Metrics
def MAPE(y_true, y_pred):
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.mean(np.abs((y_true - y_pred) / y_true)) * 100

def MRE(y_true, y_pred, capacity):
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.mean(np.abs((y_true - y_pred))/capacity) * 100

def nMAE(y_true, y_pred):
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.mean(np.abs(y_true - y_pred))/y_true.mean() * 100

def MAE(y_true, y_pred):
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.mean(np.abs(y_true - y_pred))

def RMSE(y_true, y_pred):
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.sqrt(((y_pred - y_true) ** 2).mean())

def nRMSE(y_true, y_pred):
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.sqrt(((y_pred - y_true) ** 2).mean())/y_true.mean()*100

def cRMSE(y_true, y_pred, capacity):
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.sqrt(((y_pred - y_true) ** 2).mean())/capacity*100

In [3]:
def split_data(data,target_day):
    power_list=['pre_Power_15','pre_Power_30','pre_Power_45']
    data_merge = data.copy()
    row = target_day.copy()
    #建立三個表
    data_power = pd.DataFrame()
    data_2 = pd.DataFrame()  
    #抓取該筆資料的日期和時間
    data_power = data_merge[data_merge['date'].isin(row['date'])]
    row_time = pd.to_datetime(row['TIME_TO_INTERVAL'].values[0])
    #獲得該時間的前15,30,45分鐘
    pre_time = [row_time-datetime.timedelta(minutes=15),
                row_time-datetime.timedelta(minutes=30),
                row_time-datetime.timedelta(minutes=45)]
    for i in range(len(pre_time)):
        pre_time[i] = pre_time[i].strftime("%Y-%m-%d %H:%M:%S")
       

    #依據pre_time和pre_Radiation的時間獲得該時段的power和Radiation
    #兩天都有資料的話，會有6筆，但只取前三筆(當日)
    for h in range(0,3): 
        data_power_2 = data_power[data_power['TIME_TO_INTERVAL'].isin([pre_time[h]])].reset_index(drop=True)  

        if(len(data_power_2)==0):
            data_2[power_list[h]] = [0]
#             print('---------------',data_2[power_list[h]])
        else:
            data_2[power_list[h]] = data_power_2['Power']
            
    return data_2

In [4]:
def model_build(train_x, train_y, train_idx, test_x, test_y, test_idx, model_name):
    #模型訓練
    if model_name == 'xgb':
        model = xgb.XGBRegressor(objective='reg:squarederror',
                        learning_rate=0.01, 
                        max_depth=1,
                        colsample_bytree=0.1,
                        reg_lambda=0.01,
                        seed=1,
                        subsample=0.1,
                        min_child_weight=1,
                        n_estimators=4000).fit(train_x, train_y)
    elif model_name == 'lgb':
        model = lgb.LGBMRegressor(
               boosting_type='gbdt',
                     verbose = 0,
                     learning_rate = 0.01,
                     num_leaves = 35,
                     feature_fraction=0.8,
                     bagging_fraction= 0.9,
                     bagging_freq= 8,
                     lambda_l1= 0.6,
                     lambda_l2= 0).fit(train_x, train_y)
    elif model_name == 'svr':
        model = SVR(C=1, kernel="rbf", gamma='auto').fit(train_x, train_y)
    elif model_name == 'rvm':
        model = EMRVR(kernel="rbf", gamma='auto',verbose=True)
        model.fit(train_x, train_y)
        #joblib.dump(model,'./model/15_minute/6-17/2022_rvm_CWB_pred_15m_low.pkl')
    elif model_name == 'persistence':
        test_x = scaler_x.inverse_transform(test_x)
        test_x = test_x.reshape(-1)
        test_y = test_y.reshape(-1)
        test_idx['pred'] = test_x
        test_idx['true'] = test_y
        return test_idx



#     other_params = {'learning_rate': 0.1, 'n_estimators': 500, 'max_depth': 5, 'min_child_weight': 1, 'seed': 0,
#     'subsample': 0.8, 'colsample_bytree': 0.8, 'gamma': 0, 'reg_alpha': 0, 'reg_lambda': 1}
#     model = xgb.XGBRegressor(**other_params).fit(train_x, train_y)

# 預測
    pred_y = model.predict(test_x)
    
    
# 反正規劃
    pred_y = pred_y.reshape(-1,1)
    pred_y = scaler_y.inverse_transform(pred_y)
    pred_y = pred_y.reshape(-1)
    test_idx['pred'] = pred_y
    test_idx['true'] = test_y
    return test_idx

In [5]:
merge_data = pd.read_csv('merge_weather_power_for_train15(cwb).csv', low_memory=False)
merge_data['month'] = pd.to_datetime(merge_data ['TIME_TO_INTERVAL']).dt.month
#刪除欄位中有0的值
merge_data = merge_data.drop( index = merge_data['pre_Power_15'][merge_data['pre_Power_15'] == 0].index )
merge_data = merge_data.drop( index = merge_data['pre_Power_30'][merge_data['pre_Power_30'] == 0].index )
merge_data = merge_data.drop( index = merge_data['pre_Power_45'][merge_data['pre_Power_45'] == 0].index )
merge_data = merge_data.drop( index = merge_data['pre_Radiation_15'][merge_data['pre_Radiation_15'] == 0].index )
merge_data = merge_data.drop( index = merge_data['Radiation_0'][merge_data['Radiation_0'] == 0].index )
merge_data = merge_data.drop( index = merge_data['next_Radiation_15'][merge_data['next_Radiation_15'] == 0].index )
feature = ['pre_Power_30','pre_Power_45','pre_Radiation_15','Radiation_0','next_Radiation_15','month']
mask = ((merge_data['hour']>=6) & (merge_data['hour']<=17))
merge_data = merge_data[mask].reset_index(drop=True)
mask2 = ((merge_data['TIME_TO_INTERVAL']<='2022-10-31'))
merge_data  = merge_data[mask2]
merge_data

TIME_TO_INTERVAL        date  hour     Power  Radiation  \
0     2022-02-27 06:15:00  2022-02-27     6  0.028356   0.022222   
1     2022-02-27 06:30:00  2022-02-27     6  0.045844   0.022222   
2     2022-02-27 06:45:00  2022-02-27     6  0.586811   0.022222   
3     2022-02-27 07:00:00  2022-02-27     7  1.115156   0.200000   
4     2022-02-27 07:15:00  2022-02-27     7  1.663289   0.200000   
...                   ...         ...   ...       ...        ...   
6723  2022-10-30 14:00:00  2022-10-30    14  4.852100   0.533333   
6724  2022-10-30 14:15:00  2022-10-30    14  4.532111   0.533333   
6725  2022-10-30 14:30:00  2022-10-30    14  3.790267   0.533333   
6726  2022-10-30 14:45:00  2022-10-30    14  3.139456   0.533333   
6727  2022-10-30 15:00:00  2022-10-30    15  2.684278   0.294444   

      ClearSkyRadiation  Radiation(SDv3)(CWB)  Radiation(SDv3)(TWC)  \
0              0.010630              0.030983              0.028263   
1              0.010630              0.030983              0.028263   
2              0.010630              0.030983              0.028263   
3              0.172021              0.112595              0.153755   
4              0.172021              0.112595              0.153755   
...                 ...                   ...                   ...   
6723           0.541446              0.389972              0.365350   
6724           0.541446              0.389972              0.365350   
6725           0.541446              0.389972              0.365350   
6726           0.541446              0.389972              0.365350   
6727           0.339214              0.227049              0.204579   

      Radiation(SDv3)(OWM)  Radiation(SDv3)(MSM)  ...  Radiation(today)(IBM)  \
0                 0.011878               0.01122  ...               0.028263   
1                 0.011878               0.01122  ...               0.028263   
2                 0.011878               0.01122  ...               0.028263   
3                 0.087775               0.19449  ...               0.153755   
4                 0.087775               0.19449  ...               0.153755   
...                    ...                   ...  ...                    ...   
6723              0.441357               0.57090  ...               0.365350   
6724              0.441357               0.57090  ...               0.365350   
6725              0.441357               0.57090  ...               0.365350   
6726              0.441357               0.57090  ...               0.365350   
6727              0.276733               0.36391  ...               0.204579   

      Radiation(today)(OWM)  minute  pre_Power_15  pre_Radiation_15  \
0                  0.011878      15      0.028078          0.030983   
1                  0.011878      30      0.028356          0.030983   
2                  0.011878      45      0.045844          0.030983   
3                  0.087775       0      0.586811          0.030983   
4                  0.087775      15      1.115156          0.112595   
...                     ...     ...           ...               ...   
6723               0.441357       0      5.064478          0.471209   
6724               0.441357      15      4.852100          0.389972   
6725               0.441357      30      4.532111          0.389972   
6726               0.441357      45      3.790267          0.389972   
6727               0.276733       0      3.139456          0.389972   

      pre_Power_30  Radiation_0  pre_Power_45  next_Radiation_15  month  
0         0.028056     0.030983      0.027644           0.030983      2  
1         0.028078     0.030983      0.028056           0.030983      2  
2         0.028356     0.030983      0.028078           0.112595      2  
3         0.045844     0.112595      0.028356           0.112595      2  
4         0.586811     0.112595      0.045844           0.112595      2  
...            ...          ...           ...                ...    ...  
6723   

# 加入雲量資料

In [6]:
def cloud_sort(row):
    if(row['cloud']<0):
        row['cloud']= np.NaN
    if(row['low']<0):
        row['low']= np.NaN
    if(row['mid']<0):
        row['mid']= np.NaN
    if(row['hig']<0):
        row['hig']= np.NaN
    return row

In [7]:
# linear interpolation 線性插值
from scipy.interpolate import interp1d
def interpolate(x, kind='linear'):
    not_nan = np.logical_not(np.isnan(x))
    indices = np.arange(len(x))
#     interp = interp1d(indices[not_nan], x[not_nan], kind=kind)
    interp = interp1d(indices[not_nan], x[not_nan], kind=kind,fill_value="extrapolate")
    return interp(indices)

In [8]:
#轉為小時單位
def bulid_15minute_data(data_raw):
    data_raw['TIME_TO_INTERVAL'] = pd.to_datetime(data_raw['TIME_TO_INTERVAL'])
    data_raw_2 = data_raw.groupby(pd.Grouper(key="TIME_TO_INTERVAL",freq='15min', origin='start')).mean().reset_index()
    return data_raw_2

In [9]:
def cloud_15m(row_cloud,next_cloud):
    cloud_15 = pd.DataFrame()
    if(row_cloud['minute'][0]==10):
        cloud_15 = cloud_15.append(row_cloud,ignore_index=True)
        cloud_15 = cloud_15.append({'Date':row_cloud['Date'][0],'Hour':row_cloud['Hour'][0],'minute':15,'cloud':np.NaN,'low':np.NaN,'mid':np.NaN,'hig':np.NaN},ignore_index=True)
        cloud_15 = cloud_15.append(next_cloud,ignore_index=True)
        cloud_15 = cloud_15[['Date','Hour','minute','cloud','low','mid','hig']].reset_index(drop=True)
        cloud_15['cloud'] = interpolate(cloud_15['cloud'].values)
        cloud_15['low'] = interpolate(cloud_15['low'].values)
        cloud_15['mid'] = interpolate(cloud_15['mid'].values)
        cloud_15['hig'] = interpolate(cloud_15['hig'].values)
        cloud_15 = cloud_15.loc[1:1]
    elif(row_cloud['minute'][0]==40):
        cloud_15 = cloud_15.append(row_cloud,ignore_index=True)
        cloud_15 = cloud_15.append({'Date':row_cloud['Date'][0],'Hour':row_cloud['Hour'][0],'minute':45,'cloud':np.NaN,'low':np.NaN,'mid':np.NaN,'hig':np.NaN},ignore_index=True)
        cloud_15 = cloud_15.append(next_cloud,ignore_index=True)
        cloud_15 = cloud_15[['Date','Hour','minute','cloud','low','mid','hig']].reset_index(drop=True)
        cloud_15['cloud'] = interpolate(cloud_15['cloud'].values)
        cloud_15['low'] = interpolate(cloud_15['low'].values)
        cloud_15['mid'] = interpolate(cloud_15['mid'].values)
        cloud_15['hig'] = interpolate(cloud_15['hig'].values)
        cloud_15 = cloud_15.loc[1:1]
    elif(row_cloud['minute'][0]==30 or row_cloud['minute'][0]==0):
        cloud_15 = row_cloud[['Date','Hour','minute','cloud','low','mid','hig']]
    else:
         cloud_15[['Date','Hour','minute','cloud','low','mid','hig']] = np.nan
    return cloud_15

In [10]:
cloud = pd.read_csv(f'cloud_datas.csv', low_memory=False)
cloud.rename(columns={'time': 'minute'}, inplace=True)
cloud['Date'] = cloud['TIME_TO_INTERVAL']
cloud['Hour'] = cloud['minute']//60
cloud['minute'] = cloud['minute']%60
#使用線性插植
cloud = cloud.apply(lambda x: cloud_sort(x), axis=1)
cloud['cloud'] = interpolate(cloud['cloud'].values)
cloud['low'] = interpolate(cloud['low'].values)
cloud['mid'] = interpolate(cloud['mid'].values)
cloud['hig'] = interpolate(cloud['hig'].values)
cloud = cloud[['Date','Hour','minute','cloud','low','mid','hig']]
cloud_15minute = pd.DataFrame()
for i in tqdm(range(len(cloud)-1)):
    row_cloud = cloud.loc[i:i].reset_index(drop=True)
    next_cloud = cloud.loc[i+1:i+1].reset_index(drop=True)
    cloud_15 = cloud_15m(row_cloud,next_cloud)
    cloud_15minute = pd.concat([cloud_15minute,cloud_15],axis=0)
cloud_15minute.reset_index(drop=True)

100%|███████████████████████████████████████████████████████████████████████████| 39311/39311 [02:16<00:00, 289.01it/s]


Date  Hour  minute  cloud    low         mid    hig
0      2022-02-01   0.0     0.0  100.0  100.0  100.000000  100.0
1      2022-02-01   0.0    15.0  100.0  100.0  100.000000   69.0
2      2022-02-01   0.0    30.0  100.0  100.0  100.000000   90.0
3      2022-02-01   0.0    45.0  100.0   50.0   95.141407  100.0
4      2022-02-01   1.0     0.0  100.0    0.0   16.536278  100.0
...           ...   ...     ...    ...    ...         ...    ...
26203  2022-10-31  22.0    45.0  100.0  100.0  100.000000  100.0
26204  2022-10-31  23.0     0.0  100.0  100.0  100.000000  100.0
26205  2022-10-31  23.0    15.0  100.0  100.0  100.000000  100.0
26206  2022-10-31  23.0    30.0  100.0  100.0  100.000000  100.0
26207  2022-10-31  23.0    45.0  100.0  100.0  100.000000  100.0

[26208 rows x 7 columns]

In [11]:
cloud_15minute['TIME_TO_INTERVAL'] = pd.to_datetime(cloud_15minute.apply(
        lambda row: '{} {:02d}:{:02d}:00'.format(row['Date'], int(row['Hour']), int(row['minute'])), axis=1))
cloud_15minute = cloud_15minute[['TIME_TO_INTERVAL','cloud','low','mid','hig']].reset_index(drop=True)
merge_data['TIME_TO_INTERVAL'] = pd.to_datetime(merge_data['TIME_TO_INTERVAL'])
cloud_15minute['TIME_TO_INTERVAL'] = pd.to_datetime(cloud_15minute['TIME_TO_INTERVAL'])
merge_data = pd.merge(merge_data,cloud_15minute,on = ['TIME_TO_INTERVAL'],how="inner")   

In [12]:
merge_data

TIME_TO_INTERVAL        date  hour     Power  Radiation  \
0    2022-02-27 06:15:00  2022-02-27     6  0.028356   0.022222   
1    2022-02-27 06:30:00  2022-02-27     6  0.045844   0.022222   
2    2022-02-27 06:45:00  2022-02-27     6  0.586811   0.022222   
3    2022-02-27 07:00:00  2022-02-27     7  1.115156   0.200000   
4    2022-02-27 07:15:00  2022-02-27     7  1.663289   0.200000   
...                  ...         ...   ...       ...        ...   
6626 2022-10-30 14:00:00  2022-10-30    14  4.852100   0.533333   
6627 2022-10-30 14:15:00  2022-10-30    14  4.532111   0.533333   
6628 2022-10-30 14:30:00  2022-10-30    14  3.790267   0.533333   
6629 2022-10-30 14:45:00  2022-10-30    14  3.139456   0.533333   
6630 2022-10-30 15:00:00  2022-10-30    15  2.684278   0.294444   

      ClearSkyRadiation  Radiation(SDv3)(CWB)  Radiation(SDv3)(TWC)  \
0              0.010630              0.030983              0.028263   
1              0.010630              0.030983              0.028263   
2              0.010630              0.030983              0.028263   
3              0.172021              0.112595              0.153755   
4              0.172021              0.112595              0.153755   
...                 ...                   ...                   ...   
6626           0.541446              0.389972              0.365350   
6627           0.541446              0.389972              0.365350   
6628           0.541446              0.389972              0.365350   
6629           0.541446              0.389972              0.365350   
6630           0.339214              0.227049              0.204579   

      Radiation(SDv3)(OWM)  Radiation(SDv3)(MSM)  ...  pre_Radiation_15  \
0                 0.011878               0.01122  ...          0.030983   
1                 0.011878               0.01122  ...          0.030983   
2                 0.011878               0.01122  ...          0.030983   
3                 0.087775               0.19449  ...          0.030983   
4                 0.087775               0.19449  ...          0.112595   
...                    ...                   ...  ...               ...   
6626              0.441357               0.57090  ...          0.471209   
6627              0.441357               0.57090  ...          0.389972   
6628              0.441357               0.57090  ...          0.389972   
6629              0.441357               0.57090  ...          0.389972   
6630              0.276733               0.36391  ...          0.389972   

      pre_Power_30  Radiation_0  pre_Power_45  next_Radiation_15  month  \
0         0.028056     0.030983      0.027644           0.030983      2   
1         0.028078     0.030983      0.028056           0.030983      2   
2         0.028356     0.030983      0.028078           0.112595      2   
3         0.045844     0.112595      0.028356           0.112595      2   
4         0.586811     0.112595      0.045844           0.112595      2   
...            ...          ...           ...                ...    ...   
6626      6.078767     0.389972      4.391489           0.389972     10   
6627      5.064478     0.389972      6.078767           0.389972     10   
6628      4.852100     0.389972      5.064478           0.389972     10   
6629      4.532111     0.389972      4.852100           0.227049     10   
6630      3.790267     0.227049      4.532111           0.227049     10   

          cloud        low        mid        hig  
0      0.000000   0.000000   0.000000   0.000000  
1      0.000000   0.000000   0.000000   0.000000  
2      0.000000   0.000000   0.000000   0.000000  
3      0.000000   0.000000   0.000000   0.000000  
4      0.000000   0.000000   0.000000   0.000000  
...         ...        ...        ...        ...  
6626  90.844403  90.844403  86.143187  86.143187  
6627  91.073293  91.073293  86.489607  86.489607  
6628  91.302183  91.302183  86.836028  86.836028  
6629  91.531073  91.531073  87.182448 

In [13]:
Baoshan = pd.read_csv(f'Plant_Info_Baoshan.csv', low_memory=False)
solar_capacity = Baoshan['Capacity'][1]
solar_capacity

9.7

In [14]:
# test_split_date = '2022-05-20'
# test_split_date_2 = '2022-09-15'
test_split_date = '2022-10-01'
test_split_date_2 = '2022-10-31'
anser = []
feature = ['cloud','low','mid','hig']
result = pd.DataFrame()
for i in range(len(feature)):
# for i in range(1):
    feature_data = ['pre_Power_15','pre_Power_30','next_Radiation_15']
#     feature_data =['pre_Power_15']
    feature_data.append(feature[i])
    mask = merge_data['TIME_TO_INTERVAL']<test_split_date
    mask2 = merge_data['TIME_TO_INTERVAL']>=test_split_date
    mask3 = merge_data['TIME_TO_INTERVAL']<=test_split_date_2
    train_data = merge_data[mask]
    test_data = merge_data[(mask2&mask3)]
    print('train_data:',len(train_data),'test_data:',len(test_data))
    train_x = train_data[feature_data]
    train_y = train_data[['Power']]
    test_x = test_data[feature_data]
    test_y = test_data[['Power']]
    
    scaler_x = MinMaxScaler()
    scaler_x.fit(train_x[feature_data])
    train_x = scaler_x.transform(train_x[feature_data])
    test_x = scaler_x.transform(test_x[feature_data])
    scaler_y = MinMaxScaler()
    scaler_y.fit(train_y[['Power']])
    train_y = scaler_y.transform(train_y[['Power']])

    train_x, train_y = np.array(train_x), np.array(train_y)
    test_x, test_y = np.array(test_x), np.array(test_y)
    train_idx, test_idx = pd.DataFrame(), pd.DataFrame()  
    pred = model_build(train_x, train_y, train_idx, test_x, test_y, test_idx, 'rvm')
    pre_result=[]
    pre_result.append(round(MRE(pred['true'], pred['pred'],solar_capacity),2))
    pre_result.append(round(nRMSE(pred['true'], pred['pred']),2))
    pre_result.append(round(nMAE(pred['true'], pred['pred']),2))
    pre_result.append(round(RMSE(pred['true'], pred['pred']),2))
    pre_result.append(round(MAE(pred['true'], pred['pred']),2))
    result[feature[i]] = pre_result

train_data: 5320 test_data: 1311


C:\Users\GodZen\Anaconda3\envs\python3.6\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().

C:\Users\GodZen\Anaconda3\envs\python3.6\lib\site-packages\sklearn_rvm\em_rvm.py:324: UserWarning:

Hessian not positive definite



Iteration: 0
Alpha: [1.93778234e-03 1.00000000e-08 1.00000000e-08 ... 1.05687015e-08
 4.31822190e-08 1.02643444e-08]
Beta: 2.6810978621488654e-05
Gamma: [0.9999991  0.30722718 0.33553286 ... 0.53185442 0.88289131 0.20823363]
mu: [ 2.27168666e+01 -4.00359349e+09  4.00409596e+09 ... -3.05811775e+04
  5.15823243e+03  2.80666351e+04]
Relevance Vectors: 5320

Iteration: 1
Alpha: [1.12183409e+04 1.74769106e-01 1.74111228e-01 ... 1.22434490e-01
 5.44261166e-01 3.18129472e-01]
Beta: 109.28950879944409
Gamma: [0.00010713 0.00714329 0.00714252 ... 0.00526914 0.00127529 0.00565834]
mu: [9.77212291e-05 2.02170108e-01 2.02540679e-01 ... 2.07452089e-01
 4.84061050e-02 1.33365165e-01]
Relevance Vectors: 5320

Iteration: 2
Alpha: [1.33226811e+04 4.63066762e+00 4.59384849e+00 ... 1.86018382e+02
 7.72058854e+02 8.72103036e+03]
Beta: 109.42926006821838
Gamma: [0.00010786 0.00432637 0.00434194 ... 0.00454234 0.00105865 0.00199065]
mu: [ 8.99796798e-05  3.05660978e-02  3.07435206e-02 ... -4.94153269e-03
  

Iteration: 18
Alpha: [4.05912017e+05 2.83445720e+07 1.15055016e+08 7.36374409e+10
 8.77667555e+01 1.93453439e+05 3.28760488e+06 7.63649149e+01
 3.26321274e+02 1.82092245e+08 6.46074774e+06 4.62109692e+06
 3.67002193e+05 3.05057355e+04 8.60333404e+03 1.11597225e+08
 9.94610185e+06 8.55741166e+07 3.33886955e+10 1.96245680e+05
 3.49273887e+01 6.61010451e+02 1.61644326e+06 4.32640385e+00
 5.41775107e-02 3.18158637e+13 4.82966931e+01 2.66999305e+02
 1.13281346e+05 6.29673863e+05 2.06808109e+05 5.88500694e+06
 5.86953983e+11 7.46131917e-05 2.25937110e+11 2.56588749e+05
 8.22447478e+01 4.88863873e+02 2.11650999e+03 6.00141472e+03
 1.28908446e+03 3.83463909e+01 6.64640831e+07 6.65794739e+06
 3.99015857e+06 3.14239614e+07 4.92688643e+07 9.02360467e-04
 9.13475903e+04 6.95466593e+01 5.17347645e+02 4.79829708e+12
 3.77766648e+05 2.86399899e+04 5.22226744e+03 1.11990122e+08
 1.87012404e+00 9.61865088e+09 1.15795565e+05 3.82776700e+11
 9.71022858e+03 3.42738217e+02 2.21762448e+04 3.12927243e+03
 8.

Iteration: 20
Alpha: [5.88153100e+08 3.19801709e+04 4.46773893e+05 1.09261705e+07
 2.73955225e+02 1.12929181e+04 6.26341255e+06 3.76562000e+06
 2.62106174e+05 3.83348346e+04 1.45404137e+04 4.75261423e+07
 4.40186718e+14 6.18994050e+01 3.03197512e+03 1.43184078e+07
 5.28173069e+00 1.01455544e-01 7.78006345e+02 1.15721390e+03
 1.61772324e+07 2.23460972e+06 1.46673717e+06 1.84647669e+09
 6.97684251e-05 3.93168035e+06 9.11871228e+01 1.20618152e+03
 1.23942962e+07 2.08891075e+04 6.31727958e+03 1.12676999e+02
 6.01743213e+07 2.44515489e+07 1.40521736e+07 6.33779422e+07
 5.31632074e+07 2.31727851e-03 1.32821784e+06 7.68199229e+01
 1.30215854e+03 6.47744510e+07 6.16169465e+05 1.63900205e+05
 5.63845981e+01 9.87018246e+04 3.05866862e+04 4.50349044e+02
 6.60165165e+04 1.00799737e+05 4.61929080e+06 8.61355923e+06
 3.05112461e+03 7.41389805e+06 4.81357183e+08 7.99313526e+04
 1.47299473e+07 1.17076433e+05 3.55966867e+02 2.79654565e+04
 3.43962421e+06 1.81272460e+07 1.16683927e+05 1.77812630e+00
 1.

...

Alpha: [2.90937327e-04 5.29012619e+02 3.37314532e-01 3.85897910e-04
 1.05779333e+04 5.55533389e+07 1.08976684e+02 1.45634069e+04
 6.93482405e+02 1.00408441e+02 4.90637666e+02 3.73776479e-04
 4.49377237e+03 4.10223240e+03 3.93198516e+02 1.78464865e+07
 1.76167293e+02 1.03717587e+04 5.37713546e+00 1.08196586e-03
 1.78070160e+05 1.78191859e+03 2.15336708e-04 1.56968628e-03
 1.70922416e+06 5.28342322e+02 1.89896925e+03 4.97492462e+07
 2.54886084e+07 1.11488668e+03 2.05863338e+02 1.61511346e+07
 1.02516964e+07 1.03360724e+00 2.54658954e+02 6.37098986e-03
 2.67067644e-04 1.59586907e+03 1.70843124e+02 4.13832124e+05
 3.84275122e+05 3.18615537e+03 2.45611732e+01 4.65660170e-01
 3.99701929e+01 3.29823529e-03 3.76197531e+03 5.13104472e+07
 5.19630427e-03 8.12908506e-01 5.63919664e+05 5.24827341e+04
 6.83576526e+03 4.46041997e+01 4.09766903e-01 8.87558312e+02
 4.41175416e+05 6.44164834e+03 2.84087927e+04 1.24728934e+03
 8.49000377e+04]
Beta: 108.97936678881119
Gamma: [9.96264223e-01 6.96121693e-0

  5.49308385e-08  2.11688249e-05  4.74433118e-07]
Relevance Vectors: 47

Iteration: 140
Alpha: [2.88974526e-04 1.60408206e+02 3.84742649e-04 9.12657203e+06
 3.09372522e+06 2.37137015e+06 1.09229094e+05 1.07897664e+05
 3.73090852e-04 2.19408817e+07 2.74800044e+07 1.45041418e+06
 2.71009559e+02 8.78433581e+02 1.47455866e+00 1.07877215e-03
 4.85115609e+05 8.11453170e+02 2.14612919e-04 1.56754252e-03
 1.04374936e+07 3.76269592e+07 2.11192830e+00 9.29271549e+01
 6.41211134e-03 2.66161480e-04 1.69535823e+06 2.27916136e+05
 1.78591095e+08 7.82108374e+05 4.17640640e+03 5.57090036e-01
 1.37796490e+00 3.18032863e-03 4.29177452e+06 5.64371253e-03
 2.54248158e-01 5.39249427e+07 2.10587589e+06 3.79102786e+02
 1.16047093e+01 1.27403043e+06 9.92886500e+06 1.52010663e+07
 3.00752996e+04 1.25811840e+06]
Beta: 108.97810953156444
Gamma: [9.96262799e-01 1.67380233e-06 9.96893369e-01 3.28469465e-08
 1.45713239e-07 1.51935864e-07 2.99436926e-06 2.76343089e-06
 9.96611525e-01 1.52787542e-08 1.68132102e-08 3.

Iteration: 203
Alpha: [2.84778816e-04 3.84071244e-04 3.72649808e-04 4.35811250e+02
 1.03401670e+01 1.52071696e+02 1.05798258e-03 3.53136039e+06
 2.06364077e+02 2.14760965e-04 1.57918790e-03 1.55152822e+05
 4.62935146e+03 6.49808172e-03 2.63877378e-04 7.10688050e-01
 1.32638546e-01 2.99176761e-03 6.36312817e-03 4.42743462e+01]
Beta: 108.97700146433138
Gamma: [9.96260882e-01 9.96893872e-01 9.96618549e-01 1.08483765e-03
 3.56865785e-02 1.35288584e-03 9.92308781e-01 1.26108566e-07
 1.95651663e-03 9.96643198e-01 9.97308604e-01 1.51077562e-06
 3.34759603e-05 9.93195601e-01 9.96802946e-01 7.59718800e-01
 9.76173285e-01 9.91150653e-01 9.72873414e-01 4.34407098e-03]
mu: [-5.91480354e+01  5.09476575e+01  5.17153966e+01 -1.57773172e-03
 -5.87474039e-02  2.98267807e-03 -3.06257132e+01 -1.88973659e-07
 -3.07910658e-03 -6.81243375e+01 -2.51303915e+01  3.12047094e-06
  8.50367092e-05 -1.23630363e+01  6.14627243e+01 -1.03391999e+00
  2.71286760e+00  1.82014771e+01  1.23649730e+01  9.90540822e-03]
Rele

Iteration: 316
Alpha: [2.83869494e-04 3.80610033e-04 3.69145359e-04 1.38880932e+05
 4.62685581e-01 1.06518019e-03 2.58548326e+03 2.12433288e-04
 1.54540979e-03 6.34337118e-03 2.61745599e-04 2.73374863e+02
 1.37376995e-01 3.08130229e-03 5.76291662e-03]
Beta: 108.98117821652833
Gamma: [9.96274155e-01 9.96883833e-01 9.96667316e-01 3.65322246e-06
 8.02043575e-01 9.92554858e-01 1.62230995e-04 9.96699931e-01
 9.97553709e-01 9.92841413e-01 9.96814776e-01 2.12344489e-03
 9.79138707e-01 9.90815120e-01 9.69362285e-01]
mu: [-5.92430924e+01  5.11785369e+01  5.19615724e+01 -5.12881162e-06
 -1.31660653e+00 -3.05258495e+01 -2.50493264e-04 -6.84985140e+01
 -2.54066684e+01 -1.25106600e+01  6.17128830e+01 -2.78702720e-03
  2.66971634e+00  1.79320468e+01  1.29694712e+01]
Relevance Vectors: 15

Iteration: 317
Alpha: [2.83869277e-04 3.80609206e-04 3.69144544e-04 1.51043593e+05
 4.62581297e-01 1.06518163e-03 2.72552984e+03 2.12432748e-04
 1.54540214e-03 6.34333418e-03 2.61745095e-04 2.98390002e+02
 1.373783

Iteration: 447
Alpha: [2.83866921e-04 3.80600153e-04 3.69135610e-04 4.61409905e-01
 1.06519801e-03 2.66990039e+06 2.12426821e-04 1.54531751e-03
 6.34292647e-03 2.61739563e-04 2.70805894e+07 1.37393340e-01
 3.08156237e-03 5.76133832e-03]
Beta: 108.98119043173796
Gamma: [9.96274203e-01 9.96883852e-01 9.96667524e-01 8.04301871e-01
 9.92555658e-01 1.57125344e-07 9.96700184e-01 9.97554783e-01
 9.92840661e-01 9.96814854e-01 2.14413494e-08 9.79131429e-01
 9.90814670e-01 9.69357896e-01]
mu: [-5.92433623e+01  5.11792016e+01  5.19622640e+01 -1.32028013e+00
 -3.05256065e+01 -2.42591506e-07 -6.84995655e+01 -2.54074406e+01
 -1.25110938e+01  6.17135971e+01 -2.81382446e-08  2.66954761e+00
  1.79312860e+01  1.29712182e+01]
Relevance Vectors: 14

Iteration: 448
Alpha: [2.83866920e-04 3.80600153e-04 3.69135608e-04 4.61409946e-01
 1.06519801e-03 2.81522112e+06 2.12426820e-04 1.54531750e-03
 6.34292651e-03 2.61739562e-04 2.95669292e+07 1.37393336e-01
 3.08156234e-03 5.76133850e-03]
Beta: 108.9811904306053

In [15]:
result

cloud    low    mid    hig
0   4.84   4.89   4.94   4.87
1  24.05  24.20  24.24  24.09
2  14.70  14.86  15.01  14.79
3   0.77   0.77   0.77   0.77
4   0.47   0.47   0.48   0.47

In [16]:
print(round(MRE(pred['true'], pred['pred'],solar_capacity),2))
print(round(nRMSE(pred['true'], pred['pred']),2))
print(round(nMAE(pred['true'], pred['pred']),2))
print(round(RMSE(pred['true'], pred['pred']),2))
print(round(MAE(pred['true'], pred['pred']),2))

4.87
24.09
14.79
0.77
0.47


In [17]:
line_color = [
    '#1f77b4',  # muted blue
    '#ff7f0e',  # safety orange
    '#2ca02c',  # cooked asparagus green
    '#d62728',  # brick red
    '#9467bd',  # muted purple
    '#8c564b',  # chestnut brown
    '#e377c2',  # raspberry yogurt pink
    '#7f7f7f',  # middle gray
    '#bcbd22',  # curry yellow-green
    '#17becf'   # blue-teal
]


xtick = int(len(test_data['TIME_TO_INTERVAL'])/24)

fig_line = go.Figure()

fig_line.add_trace(go.Scatter(y = pred['true'], x=test_data['TIME_TO_INTERVAL'],
                    mode='lines',
                    name='真實值',
                    line={'dash': 'dash'},
                    line_color= '#1f77b4'))
fig_line.add_trace(go.Scatter(y = pred['pred'], x=test_data['TIME_TO_INTERVAL'],
                    mode='lines',
                    name='預測值',
                    line_color= '#ff7f0e'))
fig_line.update_layout(
    yaxis_title='發電量',
    xaxis_title='日期',
    title='彰師大汙水廠預測結果',
    font=dict(
        size=18,
    ),
#     yaxis2=dict(anchor='x', overlaying='y', side='right')
    height=450, 
    width=1500,

)

fig_line.update_xaxes(nticks=xtick)


#     fig_line.write_html(f'{folder_path}/img/{methods}_{i}.html')

fig_line.show()